In [1]:
# Import required libraries
import geopandas as gpd
import pandas as pd
import numpy as np
import plotly.express as px
import json
from shapely import wkt
from sklearn.neighbors import NearestNeighbors

## Load German Postal Code Shapefile

In [5]:
# Read the German postal code shapefile
shapefile_path = 'plz-5stellig.shp'
gdf = gpd.read_file(shapefile_path)

print(f"Loaded {len(gdf)} postal code areas")
print(f"CRS: {gdf.crs}")
print(f"\nColumns: {gdf.columns.tolist()}")

Loaded 8170 postal code areas
CRS: EPSG:4326

Columns: ['plz', 'note', 'einwohner', 'qkm', 'geometry']


In [6]:
# Find the postal code column
plz_column = None
for col in gdf.columns:
    if 'plz' in col.lower() or 'post' in col.lower():
        plz_column = col
        print(f"Found postal code column: {col}")
        break

if plz_column:
    gdf[plz_column] = gdf[plz_column].astype(str).str.zfill(5)
    print(f"\nSample postal codes: {gdf[plz_column].head().tolist()}")
else:
    print("Warning: Could not identify postal code column")

Found postal code column: plz

Sample postal codes: ['81248', '60315', '24988', '93185', '93489']


## Load Meta Commuting Zones for Germany

In [ ]:

meta_cz = pd.read_csv('../meta_commuting_zones.csv')

print(f"Total commuting zones loaded: {len(meta_cz)}")

meta_cz_de = meta_cz[meta_cz['country'] == 'Germany'].copy()

# Convert WKT geography to GeoDataFrame
meta_cz_de['geometry'] = meta_cz_de['geography'].apply(wkt.loads)

# Create GeoDataFrame
meta_cz_gdf = gpd.GeoDataFrame(meta_cz_de, geometry='geometry', crs='EPSG:4326')

print(f"Created GeoDataFrame with {len(meta_cz_gdf)} commuting zones")
print(f"CRS: {meta_cz_gdf.crs}")
print(f"\nGeometry types:")
print(meta_cz_gdf.geometry.geom_type.value_counts())

## Calculate Postal Code Centroids

In [15]:
# Project to a suitable projected CRS (EPSG:25832 for Germany/UTM zone 32N) to calculate accurate centroids
gdf_projected = gdf.to_crs(epsg=25832)

# Calculate centroids in the projected CRS (meters)
# This avoids the "Geometry is in a geographic CRS" warning
gdf_projected['centroid'] = gdf_projected.geometry.centroid

# Create the WGS84 geodataframe for later use
gdf_wgs84 = gdf.to_crs(epsg=4326)

# Project the calculated centroids back to WGS84 (lat/lon)
gdf_wgs84['centroid'] = gdf_projected['centroid'].to_crs(epsg=4326)

print(f"Calculated centroids for {len(gdf_wgs84)} postal codes")
print(f"\nSample centroids:")
print(gdf_wgs84[[plz_column, 'centroid']].head())

Calculated centroids for 8170 postal codes

Sample centroids:
     plz                   centroid
0  81248  POINT (11.40315 48.14827)
1  60315   POINT (8.67392 50.11231)
2  24988   POINT (9.42971 54.70772)
3  93185  POINT (12.54133 49.12181)
4  93489  POINT (12.59606 49.16751)


In [ ]:

import plotly.graph_objects as go
sample_gdf = gdf_wgs84.head(10).copy()

center_lat = sample_gdf['centroid'].y.mean()
center_lon = sample_gdf['centroid'].x.mean()

fig = px.choropleth_map(
    sample_gdf,
    geojson=json.loads(sample_gdf.geometry.to_json()),
    locations=sample_gdf.index,
    color=plz_column, 
    hover_name=plz_column,
    map_style="carto-positron",
    zoom=8,
    center={"lat": center_lat, "lon": center_lon},
    opacity=0.5,
    title="Sample Postal Codes with Centroids"
)

fig.add_trace(go.Scattermap(
    lat=sample_gdf['centroid'].y,
    lon=sample_gdf['centroid'].x,
    mode='markers',
    marker=dict(size=8, color='red'),
    name='Centroids',
    text=sample_gdf[plz_column],
    hoverinfo='text'
))

fig.update_layout(margin={"r":0,"t":40,"l":0,"b":0})
fig.show()

## Spatial Join: Assign Postal Codes to Commuting Zones

In [ ]:
# Create GeoDataFrame with centroids
centroids_gdf = gpd.GeoDataFrame(
    gdf_wgs84[[plz_column]],
    geometry=gdf_wgs84['centroid'],
    crs='EPSG:4326'
)

# Spatial join to find which commuting zone each centroid falls into
plz_to_cz = gpd.sjoin(
    centroids_gdf,
    meta_cz_gdf[['fbcz_id', 'name', 'geometry']],
    how='left',
    predicate='within'
)

# Count matches
matched_count = plz_to_cz['fbcz_id'].notna().sum()
unmatched_count = plz_to_cz['fbcz_id'].isna().sum()

print(f"Spatial join results:")
print(f"  ✓ Matched postal codes: {matched_count} ({matched_count/len(plz_to_cz)*100:.1f}%)")
print(f"  ✗ Unmatched postal codes: {unmatched_count} ({unmatched_count/len(plz_to_cz)*100:.1f}%)")


Spatial join results:
  ✓ Matched postal codes: 8013 (98.1%)
  ✗ Unmatched postal codes: 157 (1.9%)


## Nearest Neighbor Assignment for Unmatched Postal Codes

In [24]:
# For postal codes that don't fall within any commuting zone,
# assign them to the nearest commuting zone

if unmatched_count > 0:
    print(f"Processing {unmatched_count} unmatched postal codes...\n")
    
    unmatched_mask = plz_to_cz['fbcz_id'].isna()
    unmatched_indices = plz_to_cz[unmatched_mask].index
    unmatched_coords = np.array([
        [centroids_gdf.loc[idx, 'geometry'].x, centroids_gdf.loc[idx, 'geometry'].y]
        for idx in unmatched_indices
    ])
    
    cz_centroids = meta_cz_gdf.geometry.centroid
    cz_coords = np.array([[pt.x, pt.y] for pt in cz_centroids])
    
    # Fit nearest neighbor model using haversine distance (great circle)
    nn = NearestNeighbors(n_neighbors=1, algorithm='ball_tree', metric='haversine')
    nn.fit(np.radians(cz_coords))  # Convert to radians for haversine
    
    # Find nearest commuting zone for each unmatched postal code
    distances, indices = nn.kneighbors(np.radians(unmatched_coords))
    
    # Assign nearest commuting zones
    for i, idx in enumerate(unmatched_indices):
        nearest_cz_idx = meta_cz_gdf.index[indices[i][0]]
        plz_to_cz.loc[idx, 'fbcz_id'] = meta_cz_gdf.loc[nearest_cz_idx, 'fbcz_id']
        plz_to_cz.loc[idx, 'name'] = meta_cz_gdf.loc[nearest_cz_idx, 'name']
        plz_to_cz.loc[idx, 'index_right'] = nearest_cz_idx
    
    # Convert distances from radians to kilometers (Earth radius ≈ 6371 km)
    distances_km = distances * 6371
    
    print(f"✓ Assigned {len(unmatched_indices)} postal codes using nearest neighbor")
    print(f"\nDistance statistics (km):")
    print(f"  Mean: {distances_km.mean():.2f} km")
    print(f"  Median: {np.median(distances_km):.2f} km")
    print(f"  Max: {distances_km.max():.2f} km")
    print(f"  Min: {distances_km.min():.2f} km")
else:
    print("✓ All postal codes were successfully matched directly!")

final_matched = plz_to_cz['fbcz_id'].notna().sum()
print(f"\n✓ Total postal codes assigned: {final_matched} / {len(plz_to_cz)} (100%)")

Processing 157 unmatched postal codes...

✓ Assigned 157 postal codes using nearest neighbor

Distance statistics (km):
  Mean: 43.43 km
  Median: 38.28 km
  Max: 126.56 km
  Min: 12.26 km

✓ Total postal codes assigned: 8170 / 8170 (100%)


/var/folders/xp/g3hyl1fd0x92t_v3kl5r_q880000gp/T/ipykernel_93590/3122843561.py:14: UserWarning:

Geometry is in a geographic CRS. Results from 'centroid' are likely incorrect. Use 'GeoSeries.to_crs()' to re-project geometries to a projected CRS before this operation.




## Distribution Analysis

In [25]:
# Analyze distribution of postal codes across commuting zones
cz_distribution = plz_to_cz.groupby('name').size().sort_values(ascending=False)

print("Postal Codes per Commuting Zone\n" + "="*50)
print(f"\nTop 15 commuting zones by postal code count:")
print(cz_distribution.head(15))
print(f"\nTotal commuting zones with postal codes: {len(cz_distribution)}")
print(f"\nStatistics:")
print(f"  Mean: {cz_distribution.mean():.1f} postal codes per zone")
print(f"  Median: {cz_distribution.median():.1f} postal codes per zone")
print(f"  Max: {cz_distribution.max()} postal codes")
print(f"  Min: {cz_distribution.min()} postal codes")

Postal Codes per Commuting Zone

Top 15 commuting zones by postal code count:
name
dortmund                  348
cologne                   323
bielefeld                 181
offenbach am main         155
berlin                    144
villingen-schwenningen    116
munich                    111
stuttgart                 109
leipzig                   109
gießen                    107
augsburg                  105
wurzburg                  105
hamburg                   105
frankfurt                 103
braunschweig              102
dtype: int64

Total commuting zones with postal codes: 168

Statistics:
  Mean: 48.6 postal codes per zone
  Median: 37.5 postal codes per zone
  Max: 348 postal codes
  Min: 1 postal codes


## Prepare Data for Visualization

In [26]:
# Add postal code counts to commuting zones GeoDataFrame
cz_counts = plz_to_cz.groupby('fbcz_id').size().reset_index(name='postal_code_count')
meta_cz_viz = meta_cz_gdf.merge(cz_counts, on='fbcz_id', how='left')
meta_cz_viz['postal_code_count'] = meta_cz_viz['postal_code_count'].fillna(0).astype(int)

print(f"Prepared {len(meta_cz_viz)} commuting zones for visualization")
print(f"\nCommuting zones with postal codes: {(meta_cz_viz['postal_code_count'] > 0).sum()}")
print(f"\nGeometry types in visualization data:")
print(meta_cz_viz.geometry.geom_type.value_counts())

Prepared 168 commuting zones for visualization

Commuting zones with postal codes: 168

Geometry types in visualization data:
Polygon         144
MultiPolygon     24
Name: count, dtype: int64


## Interactive Plotly Map

This map shows German Meta Commuting Zones colored by the number of postal codes assigned to each zone. The map handles both Polygon and MultiPolygon geometries.

In [31]:
# Create interactive choropleth map
# GeoJSON format handles both Polygon and MultiPolygon geometries

cz_geojson = json.loads(meta_cz_viz.to_json())

fig = px.choropleth_mapbox(
    meta_cz_viz,
    geojson=cz_geojson,
    locations=meta_cz_viz.index,
    color='postal_code_count',
    hover_name='name',
    hover_data={
        'fbcz_id': True,
        'postal_code_count': ':,',
        'win_population': ':,.0f',
        'area': ':,.2f'
    },
    labels={
        'postal_code_count': 'Postal Codes',
        'win_population': 'Population',
        'area': 'Area (km²)',
        'fbcz_id': 'Zone ID'
    },
    mapbox_style="carto-positron",
    center={"lat": 51.1657, "lon": 10.4515},  # Center of Germany
    zoom=4.75,
    opacity=0.65,
    color_continuous_scale="Viridis",
    title="German Meta Commuting Zones - Postal Code Coverage"
)

fig.update_layout(
    height=600,
    width=1000,
    margin={"r":0, "t":50, "l":0, "b":0}
)

fig.show()

print(f"\n✓ Map created successfully")
print(f"  Zones displayed: {len(meta_cz_viz)}")
print(f"  Geometry types: Polygon ({(meta_cz_viz.geometry.geom_type == 'Polygon').sum()}), "
      f"MultiPolygon ({(meta_cz_viz.geometry.geom_type == 'MultiPolygon').sum()})")

/var/folders/xp/g3hyl1fd0x92t_v3kl5r_q880000gp/T/ipykernel_93590/1025571837.py:6: DeprecationWarning:

*choropleth_mapbox* is deprecated! Use *choropleth_map* instead. Learn more at: https://plotly.com/python/mapbox-to-maplibre/




✓ Map created successfully
  Zones displayed: 168
  Geometry types: Polygon (144), MultiPolygon (24)


## Export Results

In [32]:
# Create a mapping of unique commuting zones to numeric IDs
unique_zones = plz_to_cz[['fbcz_id', 'name']].drop_duplicates().sort_values('fbcz_id').reset_index(drop=True)
unique_zones['NumericID'] = range(1, len(unique_zones) + 1)

# Export postal code to commuting zone mapping
output_df = plz_to_cz[[plz_column, 'fbcz_id', 'name']].copy()
output_df = output_df.merge(unique_zones[['fbcz_id', 'NumericID']], on='fbcz_id', how='left')
output_df.columns = ['PostCode', 'CommutingZoneID', 'CommutingZoneName', 'NumericID']

# Reorder columns
output_df = output_df[['PostCode', 'NumericID', 'CommutingZoneID', 'CommutingZoneName']]

output_file = 'de_postal_code_to_commuting_zone.csv'
output_df.to_csv(output_file, index=False)

print(f"✓ Exported mapping to: {output_file}")
print(f"  Total mappings: {len(output_df):,}")
print(f"  Unique commuting zones: {len(unique_zones)}")
print(f"\nSample mappings:")
output_df.head(10)

✓ Exported mapping to: de_postal_code_to_commuting_zone.csv
  Total mappings: 8,170
  Unique commuting zones: 168

Sample mappings:


PostCode  NumericID CommutingZoneID CommutingZoneName
0    81248         34      Europe1689            dachau
1    60315        168       Europe987         frankfurt
2    24988         74      Europe2189         flensburg
3    93185        102      Europe2291        regensburg
4    93489        106      Europe2295              cham
5    93494        106      Europe2295              cham
6    93473        106      Europe2295              cham
7    99331        166       Europe985            erfurt
8    60312        168       Europe987         frankfurt
9    98694        159       Europe978           ilmenau

In [33]:
# Add numeric IDs to the visualization data for export
meta_cz_viz_export = meta_cz_viz.merge(unique_zones[['fbcz_id', 'NumericID']], on='fbcz_id', how='left')

# Export commuting zones with postal code counts as GeoJSON
output_geojson = 'de_commuting_zones.geojson'
meta_cz_viz_export.to_file(output_geojson, driver='GeoJSON')

print(f"✓ Exported commuting zones to: {output_geojson}")
print(f"  Includes {len(meta_cz_viz_export)} zones with numeric IDs and postal code counts")

✓ Exported commuting zones to: de_commuting_zones.geojson
  Includes 168 zones with numeric IDs and postal code counts
